In [22]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append('../src/')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [23]:
from package.logger import Timed, rlog, setup
setup("INFO")


from package import storage
import pandas as pd
from package import strtime
import folium
import os
from package.osm import osm
from package.geometa import GeoMeta

In [24]:
city_id = "Koeln"
stops_path = "../data/cleaned/stops.csv"
osm_path = osm.get_osm_path_from_city_id(city_id)


geo_meta = GeoMeta.load("../data/geometa.pkl")

with Timed.info("Reading stops"):
	other_stops_df = storage.read_gdf(stops_path)

if not os.path.exists(osm_path) and city_id:
	rlog.info("Downloading OSM data")
	osm.download_city(city_id, osm_path)
else:
	rlog.info("Using existing OSM data")

osm_reader = osm.new_osm_reader(osm_path)

with Timed.info("Getting OSM graph"):
	nodes, edges = osm.get_graph_for_city_cropped_to_boundary(osm_reader, geo_meta, "walking")

[09:38:45] INFO     Reading stops                                                                   ]8;id=24349;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=444678;file:///tmp/ipykernel_11495/3959691737.py#8\8]8;;\

           INFO     Reading stops done (0.03 seconds)                                               ]8;id=335827;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=884246;file:///tmp/ipykernel_11495/3959691737.py#8\8]8;;\

           INFO     Using existing OSM data                                                        ]8;id=364662;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=130498;file:///tmp/ipykernel_11495/3959691737.py#15\15]8;;\

           INFO     Getting OSM graph                                                              ]8;id=160018;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=861765;file:///tmp/ipykernel_11495/3959691737.py#19\19]8;;\

           INFO     Loading OSM network from cache (walking)                                       ]8;id=347091;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=817650;file:///tmp/ipykernel_11495/3959691737.py#19\19]8;;\

           INFO     Getting OSM graph done (0.30 seconds)                                          ]8;id=358114;file:///tmp/ipykernel_11495/3959691737.py\3959691737.py]8;;\:]8;id=262783;file:///tmp/ipykernel_11495/3959691737.py#19\19]8;;\

In [25]:
path_source = "/home/moritz/dev/uni/mcr-py/data/bags.pkl"

data = storage.read_any_dict(path_source)
path_manager = data["path_manager"]
# node_map = data["multi_modal_node_to_resetted_map"]
# walking_node_map = data["walking_node_to_resetted_map"]
# reverse_node_map = {v: k for k, v in node_map.items()}
# reverse_walking_node_map = {v: k for k, v in walking_node_map.items()}
# stops_df = data["stops_df"]
bags_i = data["bags_i"]

In [26]:
translation_data = storage.read_any_dict("../data/car_step_translations.pkl")
reverse_node_map = translation_data["resetted_to_multi_modal_node_map"]
node_map = translation_data["multi_modal_node_to_resetted_map"]

In [27]:
labels = pd.DataFrame(
    [
        (label.node_id, label.values[0], label.values[1], n_transfers, label)
        for n_transfers, bags in bags_i.items()
        for bag in bags.values()
        for label in bag
    ],
    columns=["osm_node_id", "time", "cost", "n_transfers", "label"],
)

labels["human_readable_time"] = labels["time"].apply(strtime.seconds_to_str_time)
labels = labels.sort_values("n_transfers")
labels = labels.drop_duplicates(subset=["osm_node_id", "time", "cost"], keep="first")
labels.drop(columns=["label"])

osm_node_id   time  cost  n_transfers human_readable_time
0       246281796  29107     0            0            08:05:07
693    1722172514  29189     0            0            08:06:29
694    1722172482  29111     0            0            08:05:11
695    8243276275  29009     0            0            08:03:29
696    2095487236  29374     0            0            08:09:34
...           ...    ...   ...          ...                 ...
4841    661333418  29092   200            2            08:04:52
4855   5107728633  29940   220            2            08:19:00
4857    246567032  29940   320            2            08:19:00
4917   7042684958  30060   320            2            08:21:00
4918   7042684958  30300   220            2            08:25:00

[3844 rows x 5 columns]

In [28]:
from package.minute_city import minute_city

In [29]:
pois = minute_city.fetch_pois_for_area(geo_meta.boundary, nodes)

In [30]:
labels["target_id_osm"] = labels["osm_node_id"]
labels["start_id_hex"] = "aaa"

In [31]:
poi_labels = minute_city.add_pois_to_labels(labels, pois)

In [32]:
# types = ["grocery", "education", "health", "banks", "parks", "sustenance", "shops"]
types = list(pois["type"].unique())

In [33]:
profiles_df = minute_city.get_profiles_df(poi_labels, types)

[09:38:46] INFO     Grouping labels                                                               ]8;id=272636;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=880541;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#73\73]8;;\

           INFO     Grouping labels done (0.01 seconds)                                           ]8;id=104461;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=453238;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#73\73]8;;\

           INFO     Calculating profiles                                                          ]8;id=217719;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=390119;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

  0%|          | 0/1 [00:00<?, ?it/s]

           INFO     Calculating profiles done (0.18 seconds)                                      ]8;id=625512;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=217840;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#81\81]8;;\

           INFO     Creating profiles dataframe                                                   ]8;id=68690;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=783839;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#92\92]8;;\

           INFO     Creating profiles dataframe done (0.01 seconds)                               ]8;id=139755;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py\minute_city.py]8;;\:]8;id=561258;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/minute_city/minute_city.py#92\92]8;;\

In [34]:
profiles_df

cost_0  cost_100  cost_220  cost_320  any_column_different  \
hex_id                                                               
aaa      496.0     376.0     376.0     376.0                  True   

        required_cost_for_optimal  
hex_id                             
aaa                           100

In [35]:
max_time = strtime.str_time_to_seconds("09:00:00")
max_cost = 1000
max_transfers = 10

valid_labels = labels[
	(labels["time"] <= max_time)
	& (labels["cost"] <= max_cost)
	& (labels["n_transfers"] <= max_transfers)
]

In [36]:
# selection = valid_labels.sample(min(1000, len(valid_labels)))

max_cost = valid_labels.cost.max()

from typing import Dict
from colorsys import hls_to_rgb

def hsl_to_hex(h: float, l: float, s: float) -> str:
    r, g, b = [int(x * 255.0) for x in hls_to_rgb(h, l, s)]
    return "#{:02x}{:02x}{:02x}".format(r, g, b)

def generate_colors_hsl(max_cost: float) -> Dict[int, str]:
    if max_cost == 0:
        return {0: "#ffcccc"}
    return {
        cost: hsl_to_hex(h=0, l=0.5 + 0.4 * (max_cost - cost) / max_cost, s=0.8)
        for cost in range(int(max_cost) + 1)
    }

colors = generate_colors_hsl(max_cost)

In [37]:
start_node_id = labels[labels.time == labels.time.min()].iloc[0].osm_node_id

In [38]:
nodes_by_id = nodes.set_index("id")
nodes_by_id["id"] = nodes_by_id.index

start_node = nodes_by_id.loc[start_node_id]

m = folium.Map(location=[start_node.lat, start_node.lon], zoom_start=13)

# for label in selection.itertuples():
for label in labels.itertuples():
	node = nodes_by_id.loc[label.osm_node_id]
	folium.CircleMarker(
		location=[node.lat, node.lon],
		radius=3,
		weight=1,
		fill=True,
		fill_color=colors[label.cost],
		fill_opacity=1,
		color="black",
		popup=f"{label.human_readable_time} ({label.cost})",
	).add_to(m)

folium.CircleMarker(
	location=[start_node.lat, start_node.lon],
	radius=5,
	weight=1,
	fill=True,
	fill_color="green",
	fill_opacity=1,
	color="black",
	popup=f"Start",
).add_to(m)

m

In [39]:
from package.mcr.path import Path, GTFSPath, PathType

translator_map = {
    # PathType.WALKING: reverse_walking_node_map,
    # PathType.CYCLING_WALKING: reverse_node_map,
    PathType.DRIVING_WALKING: reverse_node_map,
    # PathType.PUBLIC_TRANSPORT: None,
}
no_prefix_reverse_node_map = {
    k: int(v[1:]) for k, v in reverse_node_map.items()
}
no_prefix_reverse_node_map = {k: int(v[1:])  for k, v in reverse_node_map.items()}
no_prefix_translator_map = {
    PathType.DRIVING_WALKING: no_prefix_reverse_node_map,
    PathType.PUBLIC_TRANSPORT: None,
}

In [40]:
result_bags = bags_i[1]

In [41]:
walking_result_bags_flat = []
for node_id, bag in result_bags.items():
	for label in bag:
		walking_result_bags_flat.append((node_id, label))

In [42]:
path_objs_with_ids = pd.Series(
    list(
        map(
            lambda x: (
                x[0],
                path_manager.reconstruct_and_translate_path_for_label(
                    x[1], no_prefix_translator_map
                ),
            ),
            walking_result_bags_flat[:10000],
        )
    )
)
node_ids, path_objs = list(zip(*path_objs_with_ids))
path_objs[:3]

KeyError: <PathType.WALKING: 'walking'>

In [ ]:
path_objs[0]

[Path(path_type=PathType.DRIVING_WALKING, path=[394001227, 1679917802, 4394977417, 2694582111, 4297860764, 266709751, 8805331129, 737784943, 266709711, 626052074, 3141997563, 737845925, 266710405, 2427289544, 4297860767, 2116624890, 3141997564, 276278173, 734098359, 2285985235, 279486552, 280124803, 943958005, 8789517655, 943957929, 671213002, 733934973, 315117901, 671213003, 2116634417, 26110723, 627998733, 3190145352, 406937317, 8789517653, 2116641930, 2116641928, 2427287508, 279166995, 5338775614, 8789517656, 5338775615, 2116641932, 2427289541, 3190145355, 279167057, 5338775612, 667027425, 1679918212, 2116645220, 279166998, 3447314049, 279167348, 8254554431, 8254554432, 3190145357, 8254554430, 2427289542, 279167346, 8254554429, 279166996, 2159999733, 1679918259, 315118775, 8254554447, 1462694008, 279231485, 3190145358, 395576169, 1679918288, 315119693, 8254554484, 654454038, 661087237, 2645720096, 654454041, 8254554491, 8254554506, 8254554524, 8254554518, 654454101, 3447307341, 6544

In [ ]:
reverse_node_map[35781]

'D394001227'

In [ ]:
labels.drop(columns=["label"])

osm_node_id   time  cost  n_transfers human_readable_time  \
0      8254554550  28876    38            0            08:01:16   
3279    266712495  28830    19            0            08:00:30   
3278    266712495  29227     0            0            08:07:07   
3277   3734989924  28864    38            0            08:01:04   
3276   3734989924  28928    19            0            08:02:08   
...           ...    ...   ...          ...                 ...   
1635   8634843176  29017     0            0            08:03:37   
1634   5375654928  28837    19            0            08:00:37   
1633   8541426514  28827    19            0            08:00:27   
1639   1539888990  28833    19            0            08:00:33   
1632   4360133865  28836    19            0            08:00:36   

      target_id_osm start_id_hex  
0        8254554550          aaa  
3279      266712495          aaa  
3278      266712495          aaa  
3277     3734989924          aaa  
3276     3734989924          aaa  
...             ...          ...  
1635     8634843176          aaa  
1634     5375654928          aaa  
1633     8541426514          aaa  
1639     1539888990          aaa  
1632     4360133865          aaa  

[4913 rows x 7 columns]

In [ ]:
import random
i = random.sample(list(labels.osm_node_id.unique()), 1)[0]
# i = 3922625314
print(i)
selection = labels[labels.osm_node_id == i]
selection.drop(columns=["label"])

1679798523


osm_node_id   time  cost  n_transfers human_readable_time  \
2924   1679798523  28856    19            0            08:00:56   

      target_id_osm start_id_hex  
2924     1679798523          aaa

In [ ]:
from folium import plugins
from folium.plugins import HeatMap

In [ ]:
start_time = strtime.str_time_to_seconds("08:00:00")

In [ ]:
def format_meta(meta, previous_meta):
	values = meta["values"]
	arrival_time = values[0]
	cost = values[1]

	if previous_meta:
		previous_values = previous_meta["values"]
		previous_arrival_time = previous_values[0]
		previous_cost = previous_values[1]
		
		arrival_time -= previous_arrival_time
		cost -= previous_cost
	else:
		arrival_time -= start_time

	return f"{strtime.seconds_to_str_time(arrival_time)} ({cost})"

In [ ]:
toloop = selection

# stops_by_id = stops_df.set_index("stop_id")
sample_label = selection.iloc[0]
sample_node_id = sample_label.osm_node_id
nodes_by_id = nodes.set_index("id")
nodes_by_id["id"] = nodes_by_id.index
sample_node = nodes_by_id.loc[sample_node_id]

m = folium.Map(location=[sample_node.lat, sample_node.lon], zoom_start=13)

for row in toloop.itertuples():
    label = row.label
    end_node_id = row.osm_node_id
    end_node = nodes_by_id.loc[end_node_id]

    folium.CircleMarker(
        location=[end_node.lat, end_node.lon],
        popup=f"End: {end_node_id}",
        color="red",
        radius=3,
    ).add_to(m)

    paths = path_manager.reconstruct_and_translate_path_for_label(label, translator_map)
    for i, path in enumerate(paths):
        if isinstance(path, Path):
            if path.path == []:
                continue
            cycling_path_nodes = [
                nodes_by_id.loc[int(node_id[1:])]
                for node_id in path.path
                if node_id[0] == "D"
            ]
            walking_path_nodes = [
                nodes_by_id.loc[int(node_id[1:])]
                for node_id in path.path
                if node_id[0] == "W"
            ]
            path_lat_lon = [(node.lat, node.lon) for node in cycling_path_nodes]
            previous_meta = paths[i - 1].meta if i > 0 else None
            meta = format_meta(path.meta, previous_meta)
            if path_lat_lon != []:
                folium.PolyLine(
                    path_lat_lon, color="blue", weight=2, popup=str(meta)
                ).add_to(m)
            path_lat_lon = [(node.lat, node.lon) for node in walking_path_nodes]
            if path_lat_lon != []:
                folium.PolyLine(
                    path_lat_lon, color="red", weight=2, popup=str(meta)
                ).add_to(m)
        elif isinstance(path, GTFSPath):
            raise Exception("GTFSPath not supported")
            start_stop_id = path.start_stop_id
            end_stop_id = path.end_stop_id
            start_stop = stops_by_id.loc[start_stop_id]
            end_stop = stops_by_id.loc[end_stop_id]
            trip = path.trip_id
            if len(trip) >= 10:
                trip = trip[:10] + "..."

            previous_meta = paths[i - 1].meta if i > 0 else None
            line_msg = f"Trip: {trip}\n---\n {format_meta(path.meta, previous_meta)}"

            path_lat_lon = [
                (float(start_stop.stop_lat), float(start_stop.stop_lon)),
                (float(end_stop.stop_lat), float(end_stop.stop_lon)),
            ]
            folium.PolyLine(
                path_lat_lon,
                color="green",
                weight=2,
                popup=line_msg,
            ).add_to(m)

            folium.CircleMarker(
                location=[float(start_stop.stop_lat), float(start_stop.stop_lon)],
                popup=f"Start: {start_stop.stop_name}",
                color="green",
                radius=3,
            ).add_to(m)
            folium.CircleMarker(
                location=[float(end_stop.stop_lat), float(end_stop.stop_lon)],
                popup=f"End: {end_stop.stop_name}",
                color="green",
                radius=3,
            ).add_to(m)
        else:
            raise Exception("Unknown path type")

m
